# Homework 3
<div class="alert alert-info">
    Note: in this notebook, we present two different methods of solving the problems presented in the homework: a 'manual' approach, in which we interpret the results of elliptic-curve additions ourselves, and an algorithmic approach, in which the problems are solved using a code-only approach. We would appreciate it if you could give us some insight into what kind of solution would be recommended/required on the exam. <i>At the end of this notebook, we ask some questions about this.</i>
</div>

## Exercise 1
First, let us construct some of the mathematical tools we need to work with. While this is not strictly necessary, it can help us to gain some insight into the problem. In addition, it can help us later; we can then perform the additions on the elliptic curve on the computer.

In [1]:
# Define the finite field over which the curve is taken.
Fp = GF(43)
Fp

Finite Field of size 43

In [2]:
# Define our elliptic curve.
E = EllipticCurve(Fp, [1, 3])
E

Elliptic Curve defined by y^2 = x^3 + x + 3 over Finite Field of size 43

In [3]:
print("This curve has", len(E.points()), "points.")

This curve has 47 points.


In [4]:
# Define the point P, and verify it has order 47.
P = E(19, 42)
print("P is the point", P)
print("order of P =", P.order())

P is the point (19 : 42 : 1)
order of P = 47


In [5]:
help(discrete_log)

Help on function discrete_log in module sage.groups.generic:

discrete_log(a, base, ord=None, bounds=None, operation='*', identity=None, inverse=None, op=None)
    Totally generic discrete log function.
    
    INPUT:
    
    - ``a``    - group element
    - ``base`` - group element (the base)
    - ``ord``  - integer (multiple of order of base, or ``None``)
    - ``bounds`` - a priori bounds on the log
    - ``operation`` - string: '*', '+', 'other'
    - ``identity`` - the group's identity
    - ``inverse()`` - function of 1 argument ``x`` returning inverse of ``x``
    - ``op()`` - function of 2 arguments ``x``, ``y`` returning ``x*y`` in group
    
    ``a`` and ``base`` must be elements of some group with identity
    given by identity, inverse of ``x`` by ``inverse(x)``, and group
    operation on ``x``, ``y`` by ``op(x,y)``.
    
    If operation is '*' or '+' then the other
    arguments are provided automatically; otherwise they must be
    provided by the caller.
    
    O

In [6]:
PA = E(28,15)
PA

(28 : 15 : 1)

In [7]:
# To check our later results, we compute
# the discrete log with respect to base P of the point PA.
P.discrete_log(PA)

9

### Exercise 1a

#### 'Manual' approach

We have that the order of the group is $47$. Hence, we want to take $m=\left\lfloor\sqrt{47}\right\rfloor=6$ for the BSGS algorithm.
For our baby steps, we hence have to compute the points $0P$, $1P$, $2P$, $3P$, $4P$ and $5P$.

In [8]:
m = floor(sqrt(E.order()))

In [9]:
P0 = 0*P
P0

(0 : 1 : 0)

In [10]:
P1 = 1*P
P1

(19 : 42 : 1)

In [11]:
P2 = P1 + P
P2

(36 : 13 : 1)

In [12]:
P3 = P2 + P
P3

(29 : 13 : 1)

In [13]:
P4 = P3 + P
P4

(9 : 15 : 1)

In [14]:
P5 = P4 + P
P5

(21 : 30 : 1)

Hence, we have the following points for our baby steps, when written in the form $(iP, i)$:
$$(P_\infty, 0)$$
$$((19,42),1)$$
$$((36,13),2)$$
$$((29,13),3)$$
$$((9,15),4)$$
$$((21,30),5)$$

Next, we compute $R=mP=6P$:

In [15]:
R = P5 + P

# Let's quickly check whether nothing is going wrong...
assert m*P == R
R

(39 : 35 : 1)

Now, we have to perform the giant steps. To this end, we set $j=0$, $Q=P_A$ and repeatedly add $R=mP$ to $Q$ (increasing $j$ in the process), until we arrive at one of the baby-step points.

In [16]:
Q = PA
j = 0
Q

(28 : 15 : 1)

We see that the point $(28,15)$ is not in any of the baby-step points. Hence, we continue.

In [17]:
Q = Q + R
j += 1
Q, j

((12 : 18 : 1), 1)

We see that the point $(12,18)$ is not in any of the baby-step points. Hence, we continue.

In [18]:
Q = Q + R
j += 1
Q, j

((41 : 37 : 1), 2)

We see that the point $(41,37)$ is not in any of the baby-step points. Hence, we continue.

In [19]:
Q = Q + R
j += 1
Q, j

((7 : 40 : 1), 3)

We see that the point $(7,40)$ is not in any of the baby-step points. Hence, we continue.

In [20]:
Q = Q + R
j += 1
Q, j

((10 : 29 : 1), 4)

We see that the point $(10,29)$ is not in any of the baby-step points. Hence, we continue.

In [21]:
Q = Q + R
j += 1
Q, j

((17 : 17 : 1), 5)

We see that the point $(17,17)$ is not in any of the baby-step points. Hence, we continue.

In [22]:
Q = Q + R
j += 1
Q, j

((36 : 30 : 1), 6)

We see that the point $(36,30)$ is not in any of the baby-step points. Hence, we continue.

In [23]:
Q = Q + R
j += 1
Q, j

((9 : 15 : 1), 7)

The point $(9,15)$ is in one of the targets from the baby-step points; we see that this point is the same as the point for which $i=4$ in the baby steps.

Hence, we can compute the value of $a$ using the formula from the lecture; since we have that $P_A+7R = 4P$, and we also have that $R=mP=6P$, we get $aP+7mP=4P$, which gives us that $a+7\cdot 6 = 4$, which results in $a = 4-42 = -38$, and taking this $\mod n$, we obtain that $a=47-38=9$.

In [24]:
n = E.order()
i = 4
a = mod(i-j*m, n)
a

9

#### Algorithmic approach

Another approach to the problem is to implement the BGSP algorithm entirely:

In [25]:
# Normal weierstrass curve addition

# c4 = 1
# c6 = 3
# x = u
# y = v

INF = "INF"
P_INF = (INF, INF)

def check_point(p1, p, c4, c6):
    """
    Check if point is on curve
    """
    u,v  = p1
    return mod(v^2,p) == mod(u^3 + c4 * u + c6  ,p)

def add_points(p1,p2, p, c4 = 1,c6 = 3):
    """
    NOTE: c6 is not actually needed for calculation
    
    p1: tuple with (u,v)
    p2: tuple with (u,v)
    p: modulo p
    
    returns p3 as tuple with (u,v)
    """
    u1, v1 = p1
    u2, v2 = p2
    
    # sanity check
    
    if p1 != P_INF:
        assert check_point(p1, p, c4, c6)
    
    if p2 != P_INF:
        assert check_point(p2, p, c4, c6)
    
    # case 1: p1 is P_inf
    if v1 == P_INF:
        return p2
    elif v2 == P_INF: 
        return p1
    elif  u1==u2 and v1 == (-1*v2):
        return P_INF
    elif u1==u2 and v1==v2:
        # v1==v2 is actually implied by u1==u2
        # more or less a sanity check
        l = (3*u1^2 + c4) / 2*v1
    else:
        l = (v1-v2) / (u1-u2)
    
    u3 = l^2 - u1 - u2 
    v3 = l*(u1-u3) - v1
    return mod(u3,p), mod(v3,p)

# Curve and Field params
p = 43
c4 = 1 
c6 = 3

P = (19, 42)
PA = (28, 15)

order_P = 47

nP = (19, -42)

assert check_point(P, p, c4, c6)
assert check_point(PA, p, c4, c6)
# Check 
assert add_points(P, nP, p) == P_INF

In [26]:
def BSGS(p, pa, n, prime, c4, c6):
    """
    p, pa : Known points, where a*p = pa
    n : order of p
    prime: Field param
    
    c4, c6: curve params
    """
    
    m = floor(sqrt(n))
    print("[*] Starting BSGS with m:{}".format(m))
    bs_dict = {}
    bs_dict[P_INF] = 0
    bs_dict[p] = 1 
    
    # Baby - Step
    p_temp = p
    for i in range(2, m):
        p_temp = add_points(p_temp, p, prime)
        bs_dict[p_temp] = i
    
    # Giant - Step
    ## p_temp is at i=m-1 and p_temp = i*P = (m-1)*P
    ## R therefore should be m*P
    R = add_points(p_temp, p, prime)
    
    j = 0
    Q = pa
    print("[*] Done with BS, starting with GS with j:{} Q:{}".format(j,Q))
    while Q not in bs_dict:
        j += 1
        Q = add_points(Q, R, prime)
    
    i = bs_dict[Q]
    
    a = mod(i - j * m, n)
    # Finished loop 
    print("[*] Result: i- {}, j - {} => a - {}".format(i, j, a))
    return a

a_got = BSGS(P,PA, order_P, p, c4, c6)

[*] Starting BSGS with m:6
[*] Done with BS, starting with GS with j:0 Q:(28, 15)
[*] Result: i- 4, j - 7 => a - 9


In [27]:
# Verify a 

pa_got = P
for i in range(1, a_got):
    if pa_got == PA:
        print("a is {}".format(i))
        break
    #print("{} is point {}".format(i, pa_got))
    pa_got = add_points(pa_got, P, p)

assert pa_got == PA

### Exercise 1b

At this point, we have to re-initialize some parameters which were changed in the algorithmic approach.

In [28]:
Fp = GF(43)
E = EllipticCurve(Fp, [1, 3])
P = E(19, 42)
PA = E(28,15)

#### 'Manual' approach

To compute the discrete logarithm using Pollard's rho method with Floyd's cycle-finding algorithm, we first compute the point $W_0$, which is given as $5P_A$. After that, we compute the points $W_1, W_2, W_3, ...$. We continue computing such points $W_i$ until we find a point $W_{2i}$ for which it holds that $W_{2i}=W_i$. In that case, we have that $S_i=F_i$, or, put differently, the slow and fast walks have reached the same point. From such points, it is possible to compute the value of $a$ (the solution to the discrete logarithm problem) by decomposing both points $W_j$ into the form $b_j P + c_j P_A = b_j P + c_j a P$, putting both points equal and solving the resulting equation for $a$ (modulo the number of points on the elliptic curve).

In [29]:
S0 = 5 * PA
F0 = 5 * PA
W0 = 5 * PA
W0

(36 : 30 : 1)

In [30]:
# simple helper function that computes s(W); that is,
# it computes the remainder of the input point's x-coordinate divided by 3.
def s(W):
    return mod(W[0], 3)

In [31]:
# To verify, let's compute s(W0), which should return 0
# since 36/3 = 0 mod 3
s(W0)

0

In [32]:
# initial values of b & c
b = 0
c = 5

In [33]:
b0 = b
c0 = c

##### First step: computing $W_1=S_1$

In [34]:
# for W0, we have that the remainder is given by
s(W0)

0

In [35]:
# Hence, we obtain that
W1 = W0 + P
b = b + 1
c = c

In [36]:
# Save our results so far
S1 = W1
b1 = b
c1 = c

In [37]:
W1

(19 : 1 : 1)

##### Second step: computing $W_2=S_2=F_1$

In [38]:
# for W1, we have that the remainder is given by
s(W1)

1

In [39]:
# Hence, we obtain that
W2 = W1 + PA
b = b
c = c + 1

In [40]:
# Save our results so far
S2 = W2
F1 = W2
b2 = b
c2 = c

In [41]:
W2

(17 : 26 : 1)

In [42]:
# Check whether we are finished
F1 == S1

False

##### Third step: computing $W_3=S_3$

In [43]:
# for W2, we have that the remainder is given by
s(W2)

2

In [44]:
# Hence, we obtain that
W3 = 2*W2
b = 2*b
c = 2*c

In [45]:
# Save our results so far
S3 = W3
b3 = b
c3 = c

In [46]:
W3

(22 : 3 : 1)

##### Fourth step: computing $W_4=S_4=F_2$

In [47]:
# for W3, we have that the remainder is given by
s(W3)

1

In [48]:
# Hence, we obtain that
W4 = W3 + PA
b = b
c = c + 1

In [49]:
# Save our results so far
S4 = W4
F2 = W4
b4 = b
c4 = c

In [50]:
W4

(40 : 4 : 1)

In [51]:
# Check whether we are finished
F2 == S2

False

##### Fifth step: $W_5=S_5$

In [52]:
# for W4, we have that the remainder is given by
s(W4)

1

In [53]:
# Hence, we obtain that
W5 = W4 + PA
b = b
c = c + 1

In [54]:
# Save our results so far
S5 = W5
b5 = b
c5 = c

In [55]:
W5

(6 : 15 : 1)

##### Sixth step: $W_6=S_6=F_3$

In [56]:
# for W5, we have that the remainder is given by
s(W5)

0

In [57]:
# Hence, we obtain that
W6 = W5 + P
b = b + 1
c = c

In [58]:
# Save our results so far
S6 = W6
F3 = W6
b6 = b
c6 = c

In [59]:
W6

(33 : 5 : 1)

In [60]:
# Check whether we are finished
F3 == S3

False

##### Seventh step: $W_7=S_7$

In [61]:
# for W6, we have that the remainder is given by
s(W6)

0

In [62]:
# Hence, we obtain that
W7 = W6 + P
b = b + 1
c = c

In [63]:
# Save our results so far
S7 = W7
b7 = b
c7 = c

In [64]:
W7

(14 : 40 : 1)

##### Eighth step: $W_8=S_8=F_4$

In [65]:
# for W5, we have that the remainder is given by
s(W7)

2

In [66]:
# Hence, we obtain that
W8 = 2 * W7
b = 2*b
c = 2*c

In [67]:
# Save our results so far
S8 = W8
F4 = W8
b8 = b
c8 = c

In [68]:
W8

(40 : 4 : 1)

In [69]:
# Check whether we are finished
F4 == S4

True

<div class="alert alert-success">
    It seems we are finished; we have obtained that $F_4 = S_4$, or alternatively, that $W_8=W_4$.
</div>
From this, we can determine the value of $a$.

##### Obtaining the result
We have that $b_4 P + c_4 P_A = b_8 P + c_8 P_A$, or, alternatively, that:
$$b_4 P + c_4 a P = b_8 P + c_8 a P$$

Rewriting this and taking terms with $a$ to one side of the equation, we obtain that $(c_4-c_8)aP = (b_8-b_4)P$. This can be rewritten to obtain:

$$a \equiv \frac{b_8-b_4}{c_4-c_8}\mod N$$
where $N$ is the group order, i.e. the number of points on the elliptic curve.

In [70]:
mod((b8-b4)/(c4-c8), n)

9

This matches the result we obtained in question **a**.

#### Algorithmic approach

Again, the second approach is to implement and run the algorithm:

In [71]:
Fp = GF(43)
Fp

Finite Field of size 43

In [72]:
E = EllipticCurve(Fp, [1, 3])

In [73]:
P = E(19, 42)
N = P.order()
N

47

In [74]:
Pa = E(28, 15)

In [75]:
def next_step(W, b, c):
    sw = mod(W[0], 3)
    if (sw == 0):
        W = W + P
        b = b + 1
        c = c
    elif (sw == 1):
        W = W + Pa
        b = b
        c = c + 1
    else:
        W = W + W
        b = b + b
        c = c + c
    return (W, b, c)
    
                 
def pollard_rho_alg(W, b, c):
    b_slow = b_fast = b
    c_slow = c_fast = c
    i = 0
    i_slow, b_slow, c_slow = next_step(W, b_slow, c_slow)
    i_fast, b_fast, c_fast = next_step(*next_step(W, b_fast, c_fast))
    print("Iteration ", i)
    print(f"i_slow is {i_slow}, b_slow is {b_slow}, c_slow is {c_slow}.")
    print(f"i_fast is {i_fast}, b_fast is {b_fast}, c_fast is {c_fast}.")
    i += 1
    while (i_slow != i_fast):
        i_slow, b_slow, c_slow = next_step(i_slow, b_slow, c_slow)
        i_fast, b_fast, c_fast = next_step(*next_step(i_fast, b_fast, c_fast))
        print(f"Iteration {i}")
        print(f"i_slow is {i_slow}, b_slow is {b_slow}, c_slow is {c_slow}.")
        print(f"i_fast is {i_fast}, b_fast is {b_fast}, c_fast is {c_fast}.")
        i += 1
    a = mod( (b_fast - b_slow) / (c_slow - c_fast), N)
    return a
    
print("Solution a =", pollard_rho_alg(5 * Pa, 0, 5))

Iteration  0
i_slow is (19 : 1 : 1), b_slow is 1, c_slow is 5.
i_fast is (17 : 26 : 1), b_fast is 1, c_fast is 6.
Iteration 1
i_slow is (17 : 26 : 1), b_slow is 1, c_slow is 6.
i_fast is (40 : 4 : 1), b_fast is 2, c_fast is 13.
Iteration 2
i_slow is (22 : 3 : 1), b_slow is 2, c_slow is 12.
i_fast is (33 : 5 : 1), b_fast is 3, c_fast is 14.
Iteration 3
i_slow is (40 : 4 : 1), b_slow is 2, c_slow is 13.
i_fast is (40 : 4 : 1), b_fast is 8, c_fast is 28.
Solution a = 9


<div class="alert alert-warning">
<strong>Questions:</strong>
    <ol>
        <li>Which of the 2 solutions presented here is preferred (manual vs. algorithmic)?</li>
        <li>Would this method of implementing and running algorithms be acceptable in the context of an exam, or do we have to to go step by step without an algorithm like in the first example? We could print all of the intermediate steps durig the while loop like shown here.</li>
    </ol>
</div>